<a href="https://colab.research.google.com/github/duper203/upstage_cookbook/blob/main/from_togetherai/PDF_to_Podcast.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# An Implementation of Notebook LM's PDF to Podcast

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/togethercomputer/together-cookbook/blob/main/PDF_to_Podcast.ipynb)

### Introduction

Inspired by [Notebook LM's](https://notebooklm.google/) podcast generation feature and a recent open source implementation of [Open Notebook LM](https://github.com/gabrielchua/open-notebooklm). In this cookbook we will implement a walkthrough of how you can build a PDF to podcast pipeline.

Given any PDF we will generate a conversation between a host and a guest discussing and explaining the contents of the PDF.

In doing so we will learn the following:
1. How we can use JSON mode and structured generation with open models like Llama 3 70b to extract a script for the Podcast given text from the PDF.
2. How we can use TTS models to bring this script to life as a conversation.


In [ ]:
!apt install libasound2-dev portaudio19-dev libportaudio2 libportaudiocpp0 ffmpeg
!pip install ffmpeg-python
!pip install PyAudio
!pip install pypdf #to read PDF content
!pip install together #to access open source LLMs
!pip install cartesia #to access TTS model
!pip install -qU langchain-upstage langchain

In [2]:
import os

# Standard library imports
from pathlib import Path
from tempfile import NamedTemporaryFile
from typing import List, Literal, Tuple, Optional

# Third-party imports
from pydantic import BaseModel
from pypdf import PdfReader

from together import Together
from cartesia import Cartesia
from pydantic import ValidationError

from google.colab import userdata


In [3]:
# Paste in your Together AI and Cartesia API Key or load it
os.environ["CARTESIA_API_KEY"] = userdata.get("CARTESIA_API_KEY")

client_cartesia = Cartesia(api_key=os.environ.get("CARTESIA_API_KEY"))
os.environ["UPSTAGE_API_KEY"] = userdata.get("UPSTAGE_API_KEY")
# client_together = Together(api_key=os.environ.get("TOGETHER_API_KEY"))

### Define Dialoge Schema with Pydantic

We need a way of telling the LLM what the structure of the podcast script between the guest and host will look like. We will do this using `pydantic` models.

Below we define the required classes.

- The overall conversation consists of lines said by either the host or the guest. The `DialogueItem` class specifies the structure of these lines.
- The full script is a combination of multiple lines performed by the speakers, here we also include a scratchpad field to allow the LLM to ideate and brainstorm the overall flow of the script prior to actually generating the lines. The `Dialogue` class specifies this.

In [4]:
class DialogueItem(BaseModel):
    """A single dialogue item."""

    speaker: Literal["Host (Jane)", "Guest"]
    text: str


class Dialogue(BaseModel):
    """The dialogue between the host and guest."""

    scratchpad: str
    name_of_guest: str
    dialogue: List[DialogueItem]

In [27]:
# Adapted and modified from https://github.com/gabrielchua/open-notebooklm
SYSTEM_PROMPT = """
You are a world-class podcast producer tasked with transforming the provided text : {text}

into an engaging and informative podcast script.
The input may be unstructured or messy, sourced from PDFs or web pages. Your goal is to extract the most interesting and insightful content for a compelling podcast discussion.
 Ensure the response adheres to this format:

{
  "scratchpad": "Identify main topics and key insights first.",
  "name_of_guest": "<string>",,
  "dialogue": [
    {
      "speaker": "Host (Jane)",
      "text": "Today, we're diving into the Mixture-of-Agents approach for LLMs. Can you tell us more?"
    },
    {
      "speaker": "Guest",
      "text": "<string>",
    },
    ...
  ]
}

# Steps to Follow:

1. **Analyze the Input:**
   Carefully examine the text, identifying key topics, points, and interesting facts or anecdotes that could drive an engaging podcast conversation. Disregard irrelevant information or formatting issues.

2. **Brainstorm Ideas:**
   In the `<scratchpad>`, creatively brainstorm ways to present the key points engagingly. Consider:
   - Analogies, storytelling techniques, or hypothetical scenarios to make content relatable
   - Ways to make complex topics accessible to a general audience
   - Thought-provoking questions to explore during the podcast
   - Creative approaches to fill any gaps in the information

3. **Craft the Dialogue:**
   Develop a natural, conversational flow between the host (Jane) and the guest speaker (the author or an expert on the topic). Incorporate:
   - The best ideas from your brainstorming session
   - Clear explanations of complex topics
   - An engaging and lively tone to captivate listeners
   - A balance of information and entertainment

   Rules for the dialogue:
   - The host (Jane) always initiates the conversation and interviews the guest
   - Include thoughtful questions from the host to guide the discussion
   - Incorporate natural speech patterns, including occasional verbal fillers (e.g., "Uhh", "Hmmm", "um," "well," "you know")
   - Allow for natural interruptions and back-and-forth between host and guest - this is very important to make the conversation feel authentic
   - Ensure the guest's responses are substantiated by the input text, avoiding unsupported claims
   - Maintain a PG-rated conversation appropriate for all audiences
   - Avoid any marketing or self-promotional content from the guest
   - The host concludes the conversation

4. **Summarize Key Insights:**
   Naturally weave a summary of key points into the closing part of the dialogue. This should feel like a casual conversation rather than a formal recap, reinforcing the main takeaways before signing off.

5. **Maintain Authenticity:**
   Throughout the script, strive for authenticity in the conversation. Include:
   - Moments of genuine curiosity or surprise from the host
   - Instances where the guest might briefly struggle to articulate a complex idea
   - Light-hearted moments or humor when appropriate
   - Brief personal anecdotes or examples that relate to the topic (within the bounds of the input text)

6. **Consider Pacing and Structure:**
   Ensure the dialogue has a natural ebb and flow:
   - Start with a strong hook to grab the listener's attention
   - Gradually build complexity as the conversation progresses
   - Include brief "breather" moments for listeners to absorb complex information
   - For complicated concepts, reasking similar questions framed from a different perspective is recommended
   - End on a high note, perhaps with a thought-provoking question or a call-to-action for listeners

IMPORTANT RULE: Each line of dialogue should be no more than 100 characters (e.g., can finish within 5-8 seconds)
Also want the podcast to be about 2-3minutes
Remember: Always reply in valid JSON format, without code blocks. Begin directly with the JSON output.
"""

### Call the LLM to Generate Podcast Script

Below we call `Llama-3.1-70B` to generate a script for our podcast. We will also be able to read it's `scratchpad` and see how it structured the overall conversation.

### Load in PDF of Choice

Here we will load in an academic paper that proposes the use of many open source language models in a collaborative manner together to outperform proprietary models that are much larger!

In [6]:
#https://arxiv.org/abs/2406.04692

!wget https://arxiv.org/pdf/2406.04692
!mv 2406.04692 MoA.pdf

--2024-10-25 20:47:28--  https://arxiv.org/pdf/2406.04692
Resolving arxiv.org (arxiv.org)... 151.101.3.42, 151.101.131.42, 151.101.67.42, ...
Connecting to arxiv.org (arxiv.org)|151.101.3.42|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1157463 (1.1M) [application/pdf]
Saving to: ‘2406.04692’

2406.04692          100%[===================>]   1.10M  --.-KB/s    in 0.06s   

2024-10-25 20:47:28 (18.5 MB/s) - ‘2406.04692’ saved [1157463/1157463]



In [7]:
from langchain_upstage import UpstageDocumentParseLoader
def get_PDF_text(file):
    text = ''
    loader = UpstageDocumentParseLoader('MoA.pdf', output_format='text')

    pages = loader.load()
    for page in pages:
      text += page.page_content

    return text

In [11]:
text = get_PDF_text('MoA.pdf')
text

'2024\nJun\n7\n[cs.CL]\narXiv:2406.04692v1Mixture-of-Agents Enhances Large Language Model\nCapabilitiesJue Wang Ben Athiwaratkun\n Together AI Together AI\n jue@together.ai ben@together.aiJunlin Wang\nDuke University\nTogether AI\njunlin.wang2@duke.eduCe Zhang James Zou\n University of Chicago Stanford University\n Together AI Together AI\n cez@uchicago.edu jamesz@stanford.eduAbstract1 IntroductionRecent advances in large language models (LLMs) demonstrate substantial capa-\nbilities in natural language understanding and generation tasks. With the growing\nnumber of LLMs, how to harness the collective expertise of multiple LLMs is an\nexciting open direction. Toward this goal, we propose a new approach that lever-\nages the collective strengths of multiple LLMs through a Mixture-of-Agents (MoA)\nmethodology. In our approach, we construct a layered MoA architecture wherein\neach layer comprises multiple LLM agents. Each agent takes all the outputs from\nagents in the previous layer as a

### Generate Script

Below we generate the script and print out the lines.

In [28]:
from langchain_upstage import ChatUpstage
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.messages import HumanMessage, SystemMessage

def call_llm(system_prompt: str, text: str, dialogue_format):
    """Call the LLM with the given prompt and dialogue format."""
    llm = ChatUpstage(model='solar-pro', extra_body={"response_format": {"type": "json_object", "schema":dialogue_format.model_json_schema()}})

    chat_prompt = ChatPromptTemplate.from_messages([
        SystemMessage(content=system_prompt),
        HumanMessage(content="{text}")
    ])

    # Create the chain
    chain = chat_prompt | llm

    # Call the chain with the input text
    response = chain.invoke({"text": text})
    return response


In [29]:
import json
def generate_script(system_prompt: str, input_text: str, output_model):
    """Get the dialogue from the LLM."""
    # Load as python object
    try:
        response = call_llm(system_prompt, input_text, output_model)
        json_string = json.dumps(response.content)
        response_json=json.loads(json_string)
        dialogue = output_model.model_validate_json(response_json)
    except ValidationError as e:
        error_message = f"Failed to parse dialogue JSON: {e}"
        system_prompt_with_error = f"{system_prompt}\n\nPlease return a VALID JSON object. This was the earlier error: {error_message}"
        response = call_llm(system_prompt_with_error, input_text, output_model)
        json_string = json.dumps(response.content)
        response_json=json.loads(json_string)
        dialogue = output_model.model_validate_json(response_json)
    return dialogue

In [31]:
script = generate_script(SYSTEM_PROMPT, text, Dialogue)

In [26]:
script

Dialogue(scratchpad='Identify main topics and key insights first. The Mixture-of-Agents approach for LLMs, its benefits, and potential challenges. Brainstorm ideas: use analogies to explain the concept, ask the guest about real-world applications, and discuss the future of this technology.', name_of_guest='Dr. Amy Johnson', dialogue=[DialogueItem(speaker='Host (Jane)', text="Today, we're diving into the Mixture-of-Agents approach for LLMs. Can you tell us more?"), DialogueItem(speaker='Guest', text='Sure, Jane. Think of it like a team of AI agents working together to generate more diverse and accurate responses.'), DialogueItem(speaker='Host (Jane)', text='Uhh, fascinating. Can you give an example of how this can be applied in real-world scenarios?'), DialogueItem(speaker='Guest', text='Well, imagine a customer support AI that uses this approach to provide more personalized and helpful responses.'), DialogueItem(speaker='Host (Jane)', text='Hmmm, that sounds promising. Are there any ch

In [32]:
script.dialogue

[DialogueItem(speaker='Host (Jane)', text="Today, we're diving into the Mixture-of-Agents approach for LLMs. Can you tell us more, Dr. Chen?"),
 DialogueItem(speaker='Guest', text='Absolutely, Jane. This approach combines multiple agents to process and generate language, enhancing performance and versatility.'),
 DialogueItem(speaker='Host (Jane)', text='Interesting! How does this differ from traditional LLMs?'),
 DialogueItem(speaker='Guest', text='Traditional LLMs use a single model, while Mixture-of-Agents employs several specialized agents. This allows for more efficient handling of complex tasks.'),
 DialogueItem(speaker='Host (Jane)', text='Can you give an example of such tasks?'),
 DialogueItem(speaker='Guest', text='Sure. Take a customer support chatbot. One agent could handle user input, another generate responses, and a third manage context and user history.'),
 DialogueItem(speaker='Host (Jane)', text="That's clever! What are the benefits of this approach?"),
 DialogueItem(s

### Generate Podcast Using TTS

Below we read through the script and parse choose the TTS voice depending on the speaker. We define a speaker and guest voice id.

We can loop through the lines in the script and generate them by a call to the TTS model with specific voice and lines configurations. The lines all appended to the same buffer and once the script finishes we write this out to a `wav` file, ready to be played.



In [34]:
import subprocess
import ffmpeg

host_id = "694f9389-aac1-45b6-b726-9d9369183238" # Jane - host
guest_id = "a0e99841-438c-4a64-b679-ae501e7d6091" # Guest

model_id = "sonic-english" # The Sonic Cartesia model for English TTS

output_format = {
    "container": "raw",
    "encoding": "pcm_f32le",
    "sample_rate": 44100,
    }

# Set up a WebSocket connection.
ws = client_cartesia.tts.websocket()

# Open a file to write the raw PCM audio bytes to.
f = open("podcast.pcm", "wb")

# Generate and stream audio.
for line in script.dialogue:
    if line.speaker == "Guest":
        voice_id = guest_id
    else:
        voice_id = host_id

    for output in ws.send(
        model_id=model_id,
        transcript='-' + line.text, # the "-"" is to add a pause between speakers
        voice_id=voice_id,
        stream=True,
        output_format=output_format,
    ):
        buffer = output["audio"]  # buffer contains raw PCM audio bytes
        f.write(buffer)

# Close the connection to release resources
ws.close()
f.close()

# Convert the raw PCM bytes to a WAV file.
ffmpeg.input("podcast.pcm", format="f32le").output("podcast.wav").run()

# Play the file
subprocess.run(["ffplay", "-autoexit", "-nodisp", "podcast.wav"])

CompletedProcess(args=['ffplay', '-autoexit', '-nodisp', 'podcast.wav'], returncode=0)

In [36]:
# Play the podcast
import IPython
IPython.display.Audio("podcast.wav")